In [ ]:
#imports:
#mac: !pip3 install bs4
#mac: !pip3 install lxml
#mac: !pip3 install psycopg2
from bs4 import BeautifulSoup
import lxml
import psycopg2


  Preparing metadata (setup.py) ... done
  DEPRECATION: Building 'psycopg2' using the legacy setup.py bdist_wheel mechanism, which will be removed in a future version. pip 25.3 will enforce this behaviour change. A possible replacement is to use the standardized build interface by setting the `--use-pep517` option, (possibly combined with `--no-build-isolation`), or adding a `pyproject.toml` file to the source tree of 'psycopg2'. Discussion can be found at https://github.com/pypa/pip/issues/6334
  Created wheel for psycopg2: filename=psycopg2-2.9.10-cp312-cp312-macosx_11_0_arm64.whl size=133607 sha256=6d8e075c1516a5a558306c0944c9e28827df703c01f7d02591776751e43de2b8
  Stored in directory: /Users/merlin/Library/Caches/pip/wheels/ac/bb/ce/afa589c50b6004d3a06fc691e71bd09c9bd5f01e5921e5329b
Successfully built psycopg2


In [ ]:
#reading file and parsing into soup
xml_kategorien = '/Users/merlin/db project/DBP/data/categories.xml'
file_kategorien = open(xml_kategorien, 'r', encoding='latin1')
content_kategorien = file_kategorien.read()
kategorien_soup = BeautifulSoup(content_kategorien, "xml")
print(kategorien_soup.prettify)

<bound method Tag.prettify of <?xml version="1.0" encoding="utf-8"?>
<!-- developed from a project of the departmentof data bases of the University of Leipzig --><categories><category>Features
<category>Alle SACDs
<item>B00005Q46G</item>
<item>B00005QZL8</item>
<item>B00006WL5N</item>
<item>B00007E8UG</item>
<item>B00008PZW9</item>
<item>B00009VGD4</item>
<item>B0000A5BWW</item>
<item>B0000ADYCN</item>
<item>B0000AKP5F</item>
<item>B0000C03AH</item>
<item>B0000DC15K</item>
<item>B0000DJURY</item>
<item>B0000YO81I</item>
<item>B00020Q386</item>
<item>B0002CX4R2</item>
<item>B0002K70BA</item>
<item>B0002QXS6U</item>
<item>B0002SZVUY</item>
<item>B0002TKFS6</item>
<item>B0002UYA8G</item>
<item>B00076OMW4</item>
<item>B0007D09GK</item>
<item>B0007YP0UY</item>
<item>B0009U55PG</item></category></category>
<category>Formate
<category>Box-Sets
<category>Action, Thriller &amp; Horror
<item>B00008OP0H</item></category>
<category>Alternative
<item>B0002HSE7C</item>
<item>B000A1IE5C</item></categ

In [ ]:
#method for iterating recursively:
#   unterkategorien first, then oberkategorien

def recursiveCategories(soup):
# rekursive method to get all the categories
    #print(soup.name)
    categories = soup.findAll('category', recursive=False)
    #print(type(categories))
    for _ in categories:
        recursiveCategories(_)
        if _.find_all('category', recursive=False)==[]:
            #check ob duplicate
            #check_duplicate_query = "SELECT kategorie_id FROM Kategorien WHERE name = %s"
            #cur = conn.cursor()
            #cur.execute(check_duplicate_query, (_.contents[0].strip('\n'),))
            #duplicate_category = cur.fetchone()
            #conn.commit()
            #insert_query = "INSERT INTO unterkategorien (name) VALUES (%s);"
            #cur = conn.cursor()
            #cur.execute(insert_query, (_,))
            #conn.commit() 
            
            print("Unterkategorie: " + _.name)
            print("Unterkategorie stripped: " + _.contents[0].strip('\n'))
            print('__')
            
            
       
        else:
            #füge elemente in kategorie ein
            #check ob duplicate
            #check_duplicate_query = "SELECT name FROM kategorien WHERE name = %s"
            #cur = conn.cursor()
            #cur.execute(check_duplicate_query, (_.contents[0].strip('\n'),))
            #duplicate_category = cur.fetchone()
            #conn.commit()
            print("Oberkategorie: " + _.name)
            print("Oberkategorie stripped: " + _.contents[0].strip('\n'))
            print('__')
            
            #insert category into database
            #if not duplicate_category:
            #insert_query = "INSERT INTO kategorien (name) VALUES (%s);"
            #cur = conn.cursor()
            #cur.execute(insert_query, (_.contents[0].strip('\n'),))
            #conn.commit()
            #insert items into database
        
            







In [99]:
categories_data = kategorien_soup.find('categories')

recursiveCategories(categories_data)

Unterkategorie: category
Unterkategorie stripped: Alle SACDs
__
Oberkategorie: category
Oberkategorie stripped: Features
__
Unterkategorie: category
Unterkategorie stripped: Action, Thriller & Horror
__
Unterkategorie: category
Unterkategorie stripped: Alternative
__
Unterkategorie: category
Unterkategorie stripped: Blues
__
Unterkategorie: category
Unterkategorie stripped: Alternative Country & Americana& Country
__
Unterkategorie: category
Unterkategorie stripped: Bestseller& Country
__
Unterkategorie: category
Unterkategorie stripped: Bluegrass& Country
__
Unterkategorie: category
Unterkategorie stripped: Contemporary & New Country& Country
__
Unterkategorie: category
Unterkategorie stripped: Country Rock& Country
__
Unterkategorie: category
Unterkategorie stripped: Cowboy& Country
__
Unterkategorie: category
Unterkategorie stripped: Honky Tonk& Country
__
Unterkategorie: category
Unterkategorie stripped: Nashville Sound& Country
__
Unterkategorie: category
Unterkategorie stripped: 

In [ ]:
def insertKategorie(name):
    # Connect to your PostgreSQL database
    conn = psycopg2.connect(
    dbname="merlin",
    user="postgres",
    password="",
    host="localhost",  # or your host
    port="5435"        # default PostgreSQL port
    )
    #check for duplicate kategorien
    check_duplicate_query = "SELECT name FROM kategorien WHERE name = %s"
    cur = conn.cursor()
    cur.execute(check_duplicate_query, (name,))
    duplicate_category = cur.fetchone()
    conn.commit()
    #insert if duplicate is empty
    if not duplicate_category:
        insert_query = "INSERT INTO kategorie (name) VALUES (%s);"
        cur = conn.cursor()
        cur.execute(insert_query, (name,))
        conn.commit() 

In [ ]:
def insertUnterKategorie(name):
    # Connect to your PostgreSQL database
    conn = psycopg2.connect(
    dbname="merlin",
    user="postgres",
    password="",
    host="localhost",  # or your host
    port="5435"        # default PostgreSQL port
    )
    #check for duplicate kategorien
    check_for_kategory = "SELECT kategorie_id FROM Kategorien WHERE name = %s"
    cur = conn.cursor()
    check_id_category = cur.execute(check_for_kategory, (name,))
    conn.commit()
    ###
    if not check_id_category:
        insert_kategorie_query = "INSERT INTO kategorie (name) VALUES (%s);"
        cur = conn.cursor()
        cur.execute(insert_kategorie_query, (name,))
        check_id_category = cur.fetchone()
        conn.commit()
    #insert if duplicate is empty
    insert_unterkategorie_query = "INSERT INTO unterkategorie (kategorie_id) VALUES (%s);"
    cur = conn.cursor()
    cur.execute(insert_unterkategorie_query, (check_id_category,))
    conn.commit() 